# <center> Batch Analysis of Cosmic Rays Using Drift Tubes Detectors  <br> Benchmarking </center>
## <center> Management and Analysis of Physics Datasets </center>
<center> Maria Camila Paris Diaz, Laura Marie Schulze, Lorenzo Martinelli

In this notebook, we present the code we utilized to benchmark the performances of the analysis for the cosmic ray track reconstructon project (fully detailed in the `MAPD_Gr10_DataAnalysis.ipynb` notebook). <br>
Due to the time-consuming and sometimes erratic nature of the process, especially when experimenting with some more extreme combinations, some cells might present some inconsistencies in the order they have been run. This is because the benchmarking was performed in separate sittings, and not just once. The outputs of this notebook might appear inconsistent, but that is merely because we might have had to run the cells only partially. In particular, one cell appears like it has not been run: that is merely because, while tidying up the notebook and after having already saved the results, we inadvertently deleted it. The cell was recovered, but not re-run for obvious time-related reasons. We hope that this slight clutter of a notebook is still understandable.

In [1]:
# General utility libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools

# Dask and Dask-adjacent libraries
from distributed import Client
from distributed import SSHCluster
from dask import delayed
import dask.array as da
import dask.dataframe as dd
import dask.bytes

# Other libraries
import os
import time
from typing import Tuple
import csv

np.random.seed(13)

## Gathering the Functions and the Constants

In [2]:
####################### FUNCTIONS #######################

@delayed
def unpack_binary_word(b_word: bytes, 
                       big_endian: bool = False) -> pd.DataFrame:
    """
    This function unpacks a binary word following the convention
    used in the experiment
    
    Args:
        b_word (bytes): The raw binary data word that has to be
                        unpacked.
        big_endian (bool): A boolean flag, if True reads the 
                           data in the big endian convention,
                           otherwise in the little endian one.
                           Default is False
                           
    Returns:
        pd.DataFrame: A DataFrame containing the unpacked binary word,
                      neatly ordered
    
    """
    
    dt = np.dtype(np.uint64)
    if big_endian:
        dt = dt.newbyteorder('>')     # Big endian
    else:
        dt = dt.newbyteorder('<')     # Little endian
    word = np.frombuffer(b_word, dtype = dt)
    
    head = (word >> 61) & 0x7          
    fpga = (word >> 58) & 0x7          
    chan = (word >> 49) & 0x1FF        
    orbit = (word >> 17) & 0xFFFFFFFF  
    bx = (word >> 5) & 0xFFF           
    tdc = word & 0x1F                  
    return pd.DataFrame({
        'TDC': tdc,
        'BX': bx,
        'ORBIT': orbit,
        'CHAN': chan,
        'FPGA': fpga,
        'HEAD': head
    })
    
def read_files(file_path: str) -> dd.DataFrame:
    """
    This function reads all the files in the path using 
    dask.bytes.read_bytes, then unpacks them and creates a Dask 
    DataFrame. It uses the function unpack_binary_word to unpack
    the binary files
    
    Args:
        file_path (str): A string indicating the path to the 
                         file(s)
    
    Returns:
        ddf (dd.DataFrame): A Dask DataFrame built using the 
                            file(s).
    
    """
    
    _, blocks = dask.bytes.read_bytes(file_path,
                                      key = '<INSERT PUBLIC KEY>',
                                      secret = '<INSERT PRIVATE KEY>', 
                                      client_kwargs = {
                                         'endpoint_url': 'https://cloud-areapd.pd.infn.it:5210',
                                         'verify': False
                                      })
    ddf_del = [unpack_binary_word(block[0]) for block in blocks]
    ddf = dd.from_delayed(ddf_del)
    return ddf

# Map chambers & layers
def determine_chamber(fpga: int, chan: int) -> int:
    """
    Associates a chamber given the value in the field 'fpga' and 
    'chan' (channel)
    
    Args:
        - fpga (int): A number (either 0 or 1), describing which 
                      FPGA is used by the cell.
        - chan (int): A number (from 0 to 127), describing which
                      channel is used by the cell.
        BOTH FPGA AND CHAN ARE USED TO DETERMINE THE CHAMBER THE
        CELL BELONGS TO
    
    Returns:
        int: A number (from 0 to 3), determining the chamber.
             0 is the bottom-most chamber, while 3 is the 
             top-most.
    """
    
    if fpga == 0:
        if chan in range(0, 64):
            return 0
        elif chan in range(64, 128):
            return 1
    elif fpga == 1:
        if chan in range(0, 64):
            return 2
        elif chan in range(64, 128):
            return 3
    return '-1'

def map_chamber_and_layer(df: pd.DataFrame) -> pd.DataFrame:
    """
    Applies the determine_chamber() function in a vectorized 
    fashion and also defines the layer of the cell. Each cell 
    has 4 layers, and the simple relation between channel 
    and layer is:
    layer = channel % 4
    
    Args:
        df (pd.DataFrame): Pandas DataFrame containing the data 
                           (in this case, specifically the
                            'FPGA' and 'CHAN' fields)
    
    Returns:
        df (pd.DataFrame): The same DataFrame, but now with the 
                           added columns 'chamber' and 'layer'
    
    """
    
    
    df['chamber'] = np.vectorize(determine_chamber)(df['FPGA'], df['CHAN'])
    df['layer'] = df['CHAN'] % 4
    return df

def get_chamber_position(df: pd.DataFrame) -> pd.DataFrame:
    """
    Determines the coordinates of the center of a given cell (both
    horizontally and vertically), as well as the horizontal 
    coordinates of the left and right hits that happened within
    a cell.
    For this function, the relevant fields of the input DataFrame are
    'CHAN' and 'x_hit_mm'
    
    Args:
        df (pd.DataFrame): Pandas DataFrame containing the hit
                           information.
    Returns:
        df (pd.DataFrame): The same DataFrame, now with hit
                           information added.
    
    """
    
    # This list is used to check which condition in the 'CHAN' 
    # field is verified (i.e., which layer is being used)
    conditions = [
        (df['CHAN'] % 4 == 0),
        (df['CHAN'] % 4 == 1),
        (df['CHAN'] % 4 == 2),
        (df['CHAN'] % 4 == 3)
    ]

    # This list is used to add the x-coordinate of the center
    # of the cell, based on the conditions list
    choices_x = [
        21 + 42 * (df['CHAN'] // 4),
        21 + 42 * (df['CHAN'] // 4),
        42 + 42 * (df['CHAN'] // 4),
        42 + 42 * (df['CHAN'] // 4)
    ]

    
    # This list is used to add the z-coordinate of the center
    # of the cell, based on the conditions list
    choices_z = [
        3.5 * 13,
        1.5 * 13,
        2.5 * 13,
        0.5 * 13
    ]

    df['x_chamber_center'] = np.select(conditions, choices_x)
    df['z_loc'] = np.select(conditions, choices_z)
    df['x_right_loc'] = df['x_chamber_center'] + df['x_hit_mm']
    df['x_left_loc'] = df['x_chamber_center'] - df['x_hit_mm']

    return df

def fit_local(df: pd.DataFrame):
    """
    This function performs a fit of the local trajectory (i.e., 
    the trajectory within a single chamber) taken by a cosmic ray
    through the least-squares algorithm, so under the assumption
    that the trajectory is a straight line.
    It actually performs ALL the possible fits in a vectorized 
    fashion, then it chooses the best one based on 
    the chi-square (chooses the one with the lowest value).
    
    Args:
        df (pd.DataFrame): DataFrame containing the relevant
                           information to reconstruct a 
                           trajectory.
    
    Returns:
        pd.DataFrame: DataFrame with the information about the 
                      trajectory: coordinates of the hit,
                      slope, intercept, etc...; as well as the
                      chi-square associated with said trajectory
    """
    
    # Get events with four hits from four different layers
    if df.shape[0] in (3, 4) and len(np.unique(df['layer'])) >= 3:
        
        # Get the left and right hit positions, as well as th
        # vertical positions
        x_left = np.array(df['x_left_loc'].values)
        x_right = np.array(df['x_right_loc'].values)
        z = np.array(df['z_loc'].values)
        
        stack = np.column_stack((x_left, x_right))   # Stacks the arrays in a N x 2 array (useful later on)
        x = np.array(np.meshgrid(*stack)).reshape(df.shape[0] ,-1) # Get all possible left-right combinations for each cell involved
        
        
        A = np.vstack((z, np.ones(np.shape(z)))).T   # Get a matrix for the least squares
        
        # Least squares: save coefficients and residuals
        coeffs, residuals, _, _ = np.linalg.lstsq(A, x, rcond = None)
        
        red_chi2 = residuals / (df.shape[0] - 2 + 1e-10)  # Compute the chi-square (add a small constant to avoid division by zero)
        choice = np.argmin(red_chi2)                      # Choose the index which minimizes the chi-square
        
        # Use choice index to select the best fit
        best_red_chi2 = red_chi2[choice]
        slope = coeffs[0][choice]
        intercept = coeffs[1][choice]
        x_best = x.T[choice]
        
        result = pd.DataFrame({
            'ORBIT': [df['ORBIT'].iloc[0]],
            'chamber': [df['chamber'].iloc[0]],
            'x_chamber_center': [df['x_chamber_center'].values],
            'x_left_loc': [x_left],
            'x_right_loc': [x_right],
            'x_best': [x_best],
            'z_loc': [z],
            'slope': [slope],
            'intercept': [intercept],
            'reduced_chi2': [best_red_chi2]
        })
        
        return result
    
    # Return an empty DataFrame if the conditions aren't met
    else:
        return pd.DataFrame(columns = ['ORBIT', 'chamber',
                                       'x_chamber_center',
                                       'x_left_loc', 'x_right_loc',
                                       'x_best', 'z_loc',
                                       'slope', 'intercept', 
                                       'reduced_chi2'])        
def fit_global(df: pd.DataFrame) -> pd.DataFrame:
    """
    Fits global trajectories of cosmic rays (i.e., trajectories
    within all three interested detectors) with a similar
    approach as seen in the fit_local function. That is, we 
    are still using the least squares algorithm in a vectorized
    way.
    
    Args:
        df (pd.DataFrame): DataFrame containing the information
                           required to compute the global
                           trajectories.
                           
    Return:
        results (pd.DataFrame): DataFrame with information
                                about global trajectories
                                (hit coordinates, slope,
                                intercept, etc...)
        
    """
    
    # Get events with 3-12 hits from at least 2 different chambers
    n_hits = len(df)  # get row count
    unique_chambers = len(np.unique(df['chamber']))
    if 3 <= n_hits <= 12 and unique_chambers >= 2 :
        
        # get x and z coordinates
        x_left = np.array(df['x_left_loc'].values)
        x_right = np.array(df['x_right_loc'].values)
        z = np.array(df['z_global'].values)

        # stack x coordinates
        stack = np.column_stack((x_left, x_right))
        # create array with all possible left/right combinations
        x = np.array(np.meshgrid(*stack)).reshape(df.shape[0] ,-1) 
        
        # prepare "coefficient" matrix for lstsq
        A = np.vstack((z, np.ones(np.shape(z)))).T
        
        # get fit coefficients & residuals from lstsq
        coeffs, residuals, _, _ = np.linalg.lstsq(A, x, rcond = None)
        
        # choose option with the lowest residual error
        choice = np.argmin(residuals)
        best_residuals = residuals[choice]
        slope = coeffs[0][choice]
        intercept = coeffs[1][choice]
        x_best = x.T[choice]
        red_chi2 = best_residuals / (df.shape[0] - 2)
        
        # save results to dataframe
        result = pd.DataFrame({
            'ORBIT': [df['ORBIT'].iloc[0]],
            'x_chamber_center': [df['x_chamber_center'].values],
            'x_left_loc': [x_left],
            'x_right_loc': [x_right],
            'x_best': [x_best],
            'z': [z],
            'slope': [slope],
            'intercept': [intercept],
            'reduced_chi2': [red_chi2]
        })
        
        return result
    
    else:
        # return empty dataframe
        return pd.DataFrame(columns = ['ORBIT',
                                       'x_chamber_center',
                                       'x_left_loc', 'x_right_loc',
                                       'x_best', 'z',
                                       'slope', 'intercept', 
                                       'reduced_chi2'])

In [3]:
####################### CONSTANTS #######################

file_list = [f's3://mapd-minidt-batch/data_0000{num:02d}.dat' for num in range(30)]
extra_delay = {
    0: - 1.1,
    1: 6.4,
    2: 0.5,
    3: -2.6
}
v_drift = 53.8/1000             # [mm/ns]
Delta_t = 21 / v_drift * 1.1    # [ns]

shift_chamber_z = {
    0: 219.8,
    1: 977.3,
    2: 1035.6,
    3: 1819.8
}

meta_loc = {
    'ORBIT': 'int32',
    'chamber': 'int32',
    'x_chamber_center': 'object',
    'x_left_loc': 'object',
    'x_right_loc': 'object',
    'x_best': 'object',
    'z_loc': 'object',
    'slope': 'float32',
    'intercept': 'float32',
    'reduced_chi2': 'float32'}

meta_glob = {
    'ORBIT': 'int32',
    'x_chamber_center': 'object',
    'x_left_loc': 'object',
    'x_right_loc': 'object',
    'x_best': 'object',
    'z': 'object',
    'slope': 'float32',
    'intercept': 'float32',
    'reduced_chi2': 'float32'}



As seen in the cell above, we don't use the full dataset for this task, rather we only use 30 files out of 48 (~60%). The reason for this is twofold:
* Time constraints
* Experimentation on more extreme settings

## <center> Benchmarking </center>

The benchmarking has been carried out by varying three different parameters:
* Number of workers per machine: 1, 2, 3, 4, 5, 10
* Number of threads per machine: 2, 3, 4, 10, 30
* Number of partitions: 4, 8, 12, 16, 20, 32, 1000

In [4]:
# tuples in list options are formatted as: n_workers, nthreads
options = [(1, 2), (1, 3), (1, 4), (1, 10), (1, 30),
           (2, 2), (2, 3), (2, 4), (2, 10), (2, 30),
           (3, 2), (3, 3), (3, 4), (3, 10), (3, 30),
           (4, 2), (4, 3), (4, 4), (4, 10), (4, 30),
           (5, 2), (5, 3), (5, 4), (5, 10), (5, 30), 
           (10, 2), (10, 3), (10, 4), (10, 10), (10, 30)]


# part_numbers is number of partitions
part_numbers = [4, 8, 12, 16, 20, 32, 1_000]


df = pd.DataFrame(columns = ['n_workers', 'n_threads', 
                             'n_partitions', 'time_s'])

### COMMENT OUT THESE COMMANDS --> DON'T RUN THEM INADVERTENTLY!
# df.to_csv('task_1_times.csv')
# df.to_csv('task_2_times.csv')
# df.to_csv('task_3_times.csv')

### Task 1
Task 1 consists in the data unpacking and event selection

In [5]:
for ii, option in enumerate(options):
    for jj, N in enumerate(part_numbers):
        cluster = SSHCluster(['10.67.22.72', '10.67.22.72','10.67.22.180', '10.67.22.235'],
                            connect_options = {'username': 'parisdiaz',
                                             'password': 'VI?tl51kh',
                                             'known_hosts': None},
                            scheduler_options = {'port': 8787,
                                                'dashboard_address': ':8797'},
                            worker_options = {'n_workers': option[0],
                                             'nthreads': option[1]})
        time.sleep(5)    # Sleeping time for the cluster to properly set up
        client = Client(cluster)
        print(client)
        
        start_time = time.time()
        
        ddf = read_files(file_list)
        ddf = ddf.repartition(npartitions = N)
        ddf = ddf[ddf['HEAD'] == 2]
        ddf = ddf[ddf['CHAN'] != 138]
        ddf = ddf.map_partitions(map_chamber_and_layer)
        ddf['extra_delay_ns'] = ddf['chamber'].map_partitions(lambda x: x.map(extra_delay))
        ddf['abs_time_ns'] = 25 * ( (ddf['ORBIT'] * 3564) + ddf['BX'] + (ddf['TDC'] / 30) )
        ddf_sci = ddf[ddf['CHAN'] == 128]
        ddf_tdc = ddf[ddf['CHAN'] != 128]
        sci_counts = ddf_sci.groupby('ORBIT').size().compute().reset_index(name='sci_count')
        single_hit_orbits = sci_counts[sci_counts['sci_count'] == 1]['ORBIT']
        single_hit_sci = ddf_sci[ddf_sci['ORBIT'].isin(single_hit_orbits)]
        single_hit_tdc = ddf_tdc[ddf_tdc['ORBIT'].isin(single_hit_orbits)]
        det_with_t0 = dd.merge(single_hit_tdc, single_hit_sci[['ORBIT', 'abs_time_ns']],
                               on = 'ORBIT',
                               suffixes = ('', '_sci'))
        det_with_t0['t0'] = det_with_t0['abs_time_ns_sci'] - (95 + det_with_t0['extra_delay_ns'])
        ddf_x_hit = det_with_t0[det_with_t0['abs_time_ns'].between(det_with_t0['t0'], det_with_t0['t0'] + Delta_t)]
        ddf_x_hit['x_hit_mm'] = v_drift * (det_with_t0['abs_time_ns'] - det_with_t0['t0'])
        ddf_x_hit['x_hit_mm'] = v_drift * (det_with_t0['abs_time_ns'] - det_with_t0['t0'])
        ddf_x_hit['CHAN'] = ddf_x_hit['CHAN'].where(ddf_x_hit['CHAN'] <= 63, 
                                                    ddf_x_hit['CHAN'] - 64)
        ddf_x_hit = ddf_x_hit.map_partitions(get_chamber_position)

        
        ddf_x_hit.compute()
        
        tot_time = time.time() - start_time
        with open('task_1_times.csv', 'a') as f:
            writer = csv.writer(f)
            writer.writerow([option[0], option[1], N, tot_time])
        
        
        client.close()
        cluster.close()
        

2025-02-03 11:01:43,754 - distributed.deploy.ssh - INFO - 2025-02-03 11:01:43,753 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-02-03 11:01:43,781 - distributed.deploy.ssh - INFO - 2025-02-03 11:01:43,781 - distributed.scheduler - INFO - State start
2025-02-03 11:01:43,782 - distributed.deploy.ssh - INFO - 2025-02-03 11:01:43,782 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-ietw8i8w', purging
2025-02-03 11:01:43,785 - distributed.deploy.ssh - INFO - 2025-02-03 11:01:43,785 - distributed.scheduler - INFO -   Scheduler at:    tcp://10.67.22.72:8787
2025-02-03 11:01:44,229 - distributed.deploy.ssh - INFO - 2025-02-03 11:01:44,229 - distributed.nanny - INFO -         Start Nanny at: 'tcp://10.67.22.72:39559'
2025-02-03 11:01:44,529 - distributed.deploy.ssh - INFO - 2025-02-03 11:01:44,529 - distributed.nanny - INFO -    

<Client: 'tcp://10.67.22.72:8787' processes=3 threads=6, memory=11.63 GiB>


2025-02-03 11:02:18,204 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:18,204 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-02-03 11:02:18,230 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:18,230 - distributed.scheduler - INFO - State start
2025-02-03 11:02:18,231 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:18,231 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-0ugh9lko', purging
2025-02-03 11:02:18,233 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:18,233 - distributed.scheduler - INFO -   Scheduler at:    tcp://10.67.22.72:8787
2025-02-03 11:02:18,670 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:18,669 - distributed.nanny - INFO -         Start Nanny at: 'tcp://10.67.22.72:43577'
2025-02-03 11:02:18,672 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:18,673 - distributed.nanny - INFO -    

<Client: 'tcp://10.67.22.72:8787' processes=3 threads=6, memory=11.63 GiB>


2025-02-03 11:02:49,439 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:49,439 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-02-03 11:02:49,465 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:49,464 - distributed.scheduler - INFO - State start
2025-02-03 11:02:49,466 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:49,465 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-icww5rdu', purging
2025-02-03 11:02:49,468 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:49,468 - distributed.scheduler - INFO -   Scheduler at:    tcp://10.67.22.72:8787
2025-02-03 11:02:49,923 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:49,922 - distributed.nanny - INFO -         Start Nanny at: 'tcp://10.67.22.72:42001'
2025-02-03 11:02:50,134 - distributed.deploy.ssh - INFO - 2025-02-03 11:02:50,134 - distributed.nanny - INFO -    

...

2025-02-03 12:46:22,552 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,551 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:33149
2025-02-03 12:46:22,552 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,551 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:33149
2025-02-03 12:46:22,553 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,551 - distributed.worker - INFO -          dashboard at:         10.67.22.235:43947
2025-02-03 12:46:22,554 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,551 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-02-03 12:46:22,554 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,551 - distributed.worker - INFO - -------------------------------------------------
2025-02-03 12:46:22,554 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,551 - distributed.worker - INFO -               Threads:                         30
2025-02-03 12:46:22,555 - di

2025-02-03 12:46:22,748 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,743 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-02-03 12:46:22,749 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,743 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-m0m6yh6v
2025-02-03 12:46:22,749 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,743 - distributed.worker - INFO - -------------------------------------------------
2025-02-03 12:46:22,792 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,789 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:37615
2025-02-03 12:46:22,792 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,789 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:37615
2025-02-03 12:46:22,793 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,790 - distributed.worker - INFO -          dashboard at:         10.67.22.235:43733
2025-02-03 12:4

2025-02-03 12:46:22,904 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,903 - distributed.worker - INFO -          dashboard at:          10.67.22.72:38371
2025-02-03 12:46:22,905 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,903 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-02-03 12:46:22,905 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,903 - distributed.worker - INFO - -------------------------------------------------
2025-02-03 12:46:22,906 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,903 - distributed.worker - INFO -               Threads:                         30
2025-02-03 12:46:22,906 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,904 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-02-03 12:46:22,906 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,904 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-7u_ua4ih
2025-02-03 12:4

2025-02-03 12:46:22,965 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,962 - distributed.worker - INFO - -------------------------------------------------
2025-02-03 12:46:22,966 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,963 - distributed.worker - INFO -       Start worker at:    tcp://10.67.22.72:45025
2025-02-03 12:46:22,988 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,987 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:32777
2025-02-03 12:46:22,989 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,987 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:32777
2025-02-03 12:46:22,990 - distributed.deploy.ssh - INFO - 2025-02-03 12:46:22,987 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:45723


<Client: 'tcp://10.67.22.72:8787' processes=30 threads=900, memory=232.54 GiB>


### Task 2
Task 2 is the reconstruction of local tracks

In [5]:
for ii, option in enumerate(options):
    for jj, N in enumerate(part_numbers):
        ################################# BUILD THE CLUSTER #################################
        cluster = SSHCluster(['10.67.22.72', '10.67.22.72','10.67.22.180', '10.67.22.235'],
                            connect_options = {'username': 'parisdiaz',
                                             'password': 'VI?tl51kh',
                                             'known_hosts': None},
                            scheduler_options = {'port': 8787,
                                                'dashboard_address': ':8797'},
                            worker_options = {'n_workers': option[0],
                                             'nthreads': option[1]})
        time.sleep(5)    # Sleeping time for the cluster to properly set up
        client = Client(cluster)
        print(client)

        
        ###################################### TASK 1 ######################################
        ddf = read_files(file_list)
        ddf = ddf.repartition(npartitions = N)
        ddf = ddf[ddf['HEAD'] == 2]
        ddf = ddf[ddf['CHAN'] != 138]
        ddf = ddf.map_partitions(map_chamber_and_layer)
        ddf['extra_delay_ns'] = ddf['chamber'].map_partitions(lambda x: x.map(extra_delay))
        ddf['abs_time_ns'] = 25 * ( (ddf['ORBIT'] * 3564) + ddf['BX'] + (ddf['TDC'] / 30) )
        ddf_sci = ddf[ddf['CHAN'] == 128]
        ddf_tdc = ddf[ddf['CHAN'] != 128]
        sci_counts = ddf_sci.groupby('ORBIT').size().compute().reset_index(name='sci_count')
        single_hit_orbits = sci_counts[sci_counts['sci_count'] == 1]['ORBIT']
        single_hit_sci = ddf_sci[ddf_sci['ORBIT'].isin(single_hit_orbits)]
        single_hit_tdc = ddf_tdc[ddf_tdc['ORBIT'].isin(single_hit_orbits)]
        det_with_t0 = dd.merge(single_hit_tdc, single_hit_sci[['ORBIT', 'abs_time_ns']],
                               on = 'ORBIT',
                               suffixes = ('', '_sci'))
        det_with_t0['t0'] = det_with_t0['abs_time_ns_sci'] - (95 + det_with_t0['extra_delay_ns'])
        ddf_x_hit = det_with_t0[det_with_t0['abs_time_ns'].between(det_with_t0['t0'], det_with_t0['t0'] + Delta_t)]
        ddf_x_hit['x_hit_mm'] = v_drift * (det_with_t0['abs_time_ns'] - det_with_t0['t0'])
        ddf_x_hit['CHAN'] = ddf_x_hit['CHAN'].where(ddf_x_hit['CHAN'] <= 63, 
                                                    ddf_x_hit['CHAN'] - 64)
        ddf_x_hit = ddf_x_hit.map_partitions(get_chamber_position)


        ddf_persisted = ddf_x_hit.persist()       # Persist the dataframe to correctly time only Task 2
        
        ###################################### TASK 2 ######################################
        start_time = time.time()
        groups = ddf_persisted.groupby(['ORBIT', 'chamber'])\
                              .apply(fit_local, meta = meta_loc)

        result_local_df = groups.compute()

        result_local_df.reset_index(drop = True, inplace = True)
        tot_time = time.time() - start_time
        with open('task_2_times.csv', 'a') as f:
            writer = csv.writer(f)
            writer.writerow([option[0], option[1], N, tot_time])
                
        client.close()
        cluster.close()


2025-01-27 18:01:20,412 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:20,411 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-01-27 18:01:20,438 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:20,438 - distributed.scheduler - INFO - State start
2025-01-27 18:01:20,439 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:20,439 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-pxt70fuv', purging
2025-01-27 18:01:20,440 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:20,439 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-mwkoekfj', purging
2025-01-27 18:01:20,442 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:20,442 - distributed.scheduler - INFO -   Scheduler at:    tcp://10.67.22.72:8787
2025-01-27 18:01:20,897 - distributed.deploy.ssh - INFO - 2025-01-27 18:0

2025-01-27 18:01:21,512 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:21,505 - distributed.worker - INFO -                Memory:                   3.88 GiB
2025-01-27 18:01:21,513 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:21,505 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-35g1syfg
2025-01-27 18:01:21,514 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:21,505 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 18:01:21,519 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:21,519 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.180:46095
2025-01-27 18:01:21,587 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:21,588 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-j995r0st', purging
2025-01-27 18:01:21,588 - distributed.deploy.ssh - INFO - 2025-01-27 18:01:21,588 - distributed.diskutils - INFO - Found stale lock file 

<Client: 'tcp://10.67.22.72:8787' processes=9 threads=18, memory=34.88 GiB>


2025-01-27 18:02:29,902 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:29,902 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-01-27 18:02:29,928 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:29,928 - distributed.scheduler - INFO - State start
2025-01-27 18:02:29,929 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:29,929 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-95pvoboy', purging
2025-01-27 18:02:29,930 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:29,929 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-lzexvq91', purging
2025-01-27 18:02:29,930 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:29,929 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-6p1tk_fn', purging
2025-01-27 18:02:29,932 - di

2025-01-27 18:02:30,926 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:30,917 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-01-27 18:02:30,926 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:30,917 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 18:02:30,926 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:30,917 - distributed.worker - INFO -               Threads:                          2
2025-01-27 18:02:30,927 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:30,917 - distributed.worker - INFO -                Memory:                   3.88 GiB
2025-01-27 18:02:30,928 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:30,917 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-l0yq6whz
2025-01-27 18:02:30,929 - distributed.deploy.ssh - INFO - 2025-01-27 18:02:30,917 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 18:0

...

2025-01-27 20:40:13,140 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,114 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-_4rbcaen
2025-01-27 20:40:13,141 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,114 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 20:40:13,189 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,189 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:45841
2025-01-27 20:40:13,190 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,189 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:45841
2025-01-27 20:40:13,190 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,190 - distributed.worker - INFO -          dashboard at:         10.67.22.235:43215
2025-01-27 20:40:13,191 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,190 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-01-27 20:4

2025-01-27 20:40:13,291 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,286 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 20:40:13,291 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,286 - distributed.worker - INFO -               Threads:                         30
2025-01-27 20:40:13,291 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,286 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-01-27 20:40:13,292 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,286 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-9edqbt2u
2025-01-27 20:40:13,296 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,286 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 20:40:13,439 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,439 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.180:34699
2025-01-27 20:4

2025-01-27 20:40:13,581 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,575 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 20:40:13,611 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,611 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:40405
2025-01-27 20:40:13,612 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,611 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:40405
2025-01-27 20:40:13,613 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,611 - distributed.worker - INFO -          dashboard at:         10.67.22.235:33451
2025-01-27 20:40:13,613 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,611 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-01-27 20:40:13,614 - distributed.deploy.ssh - INFO - 2025-01-27 20:40:13,612 - distributed.worker - INFO - -------------------------------------------------
2025-01-27 20:40:13,615 - di

<Client: 'tcp://10.67.22.72:8787' processes=30 threads=900, memory=232.54 GiB>


RuntimeError: P2P shuffling 5b8468e38f9318e596741fd36fcaaad1 failed during transfer phase

### Task 3
Task 3 is the reconstruction of global tracks

In [ ]:
options = [(10, 10), (10, 30)]
part_numbers = [4, 8, 12, 16, 20, 32, 1_000]

for ii, option in enumerate(options):
    for jj, N in enumerate(part_numbers):
        ################################# BUILD THE CLUSTER #################################
        cluster = SSHCluster(['10.67.22.72', '10.67.22.72','10.67.22.180', '10.67.22.235'],
                            connect_options = {'username': 'parisdiaz',
                                             'password': 'VI?tl51kh',
                                             'known_hosts': None},
                            scheduler_options = {'port': 8787,
                                                'dashboard_address': ':8797'},
                            worker_options = {'n_workers': option[0],
                                             'nthreads': option[1]})
        time.sleep(5)    # Sleeping time for the cluster to properly set up
        client = Client(cluster)
        print(client)

        
        ###################################### TASK 1 ######################################
        ddf = read_files(file_list)
        ddf = ddf.repartition(npartitions = N)
        ddf = ddf[ddf['HEAD'] == 2]
        ddf = ddf[ddf['CHAN'] != 138]
        ddf = ddf.map_partitions(map_chamber_and_layer)
        ddf['extra_delay_ns'] = ddf['chamber'].map_partitions(lambda x: x.map(extra_delay))
        ddf['abs_time_ns'] = 25 * ( (ddf['ORBIT'] * 3564) + ddf['BX'] + (ddf['TDC'] / 30) )
        ddf_sci = ddf[ddf['CHAN'] == 128]
        ddf_tdc = ddf[ddf['CHAN'] != 128]
        sci_counts = ddf_sci.groupby('ORBIT').size().compute().reset_index(name='sci_count')
        single_hit_orbits = sci_counts[sci_counts['sci_count'] == 1]['ORBIT']
        single_hit_sci = ddf_sci[ddf_sci['ORBIT'].isin(single_hit_orbits)]
        single_hit_tdc = ddf_tdc[ddf_tdc['ORBIT'].isin(single_hit_orbits)]
        det_with_t0 = dd.merge(single_hit_tdc, single_hit_sci[['ORBIT', 'abs_time_ns']],
                               on = 'ORBIT',
                               suffixes = ('', '_sci'))
        det_with_t0['t0'] = det_with_t0['abs_time_ns_sci'] - (95 + det_with_t0['extra_delay_ns'])
        ddf_x_hit = det_with_t0[det_with_t0['abs_time_ns'].between(det_with_t0['t0'], det_with_t0['t0'] + Delta_t)]
        ddf_x_hit['x_hit_mm'] = v_drift * (det_with_t0['abs_time_ns'] - det_with_t0['t0'])
        ddf_x_hit['CHAN'] = ddf_x_hit['CHAN'].where(ddf_x_hit['CHAN'] <= 63, 
                                                    ddf_x_hit['CHAN'] - 64)
        ddf_x_hit = ddf_x_hit.map_partitions(get_chamber_position)


        ddf_persisted = ddf_x_hit.persist()       # Persist the dataframe to correctly time only Task 3
        
        ###################################### TASK 3 ######################################
        start_time = time.time()
        ddf_persisted['z_global'] = ddf_persisted['z_loc'] + ddf_persisted['chamber'].map(shift_chamber_z)
        df_GT_fresh = ddf_persisted[ddf_persisted['chamber'] != 1]
        groups_GT_fresh = df_GT_fresh.groupby('ORBIT').apply(fit_global, meta=meta_glob)
        glob_results= groups_GT_fresh.compute()
        glob_results.reset_index(drop = True, inplace = True)
        
        tot_time = time.time() - start_time
        with open('task_3_times.csv', 'a') as f:
            writer = csv.writer(f)
            writer.writerow([option[0], option[1], N, tot_time])

        
        client.close()
        cluster.close()


2025-01-29 20:43:46,065 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:46,064 - distributed.http.proxy - INFO - To route to workers diagnostics web server please install jupyter-server-proxy: python -m pip install jupyter-server-proxy
2025-01-29 20:43:46,091 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:46,091 - distributed.scheduler - INFO - State start
2025-01-29 20:43:46,092 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:46,092 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-fu0iiryf', purging
2025-01-29 20:43:46,093 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:46,092 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-sx613u1o', purging
2025-01-29 20:43:46,093 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:46,092 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-scratch-space/worker-3tqiz917', purging
2025-01-29 20:43:46,094 - di

2025-01-29 20:43:47,264 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,261 - distributed.worker - INFO -               Threads:                         10
2025-01-29 20:43:47,264 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,261 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-01-29 20:43:47,264 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,262 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-8vkt44lh
2025-01-29 20:43:47,265 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,262 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:43:47,307 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,306 - distributed.worker - INFO -       Start worker at:    tcp://10.67.22.72:42985
2025-01-29 20:43:47,307 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,306 - distributed.worker - INFO -          Listening to:    tcp://10.67.22.72:42985
2025-01-29 20:4

2025-01-29 20:43:47,466 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,464 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-iu736y_v
2025-01-29 20:43:47,466 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,465 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:43:47,467 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,466 - distributed.worker - INFO -       Start worker at:    tcp://10.67.22.72:42203
2025-01-29 20:43:47,471 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,471 - distributed.worker - INFO -          Listening to:    tcp://10.67.22.72:42203
2025-01-29 20:43:47,472 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,471 - distributed.worker - INFO -          dashboard at:          10.67.22.72:35561
2025-01-29 20:43:47,472 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,471 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-01-29 20:4

2025-01-29 20:43:47,594 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,594 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:34939
2025-01-29 20:43:47,594 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,595 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:34939
2025-01-29 20:43:47,595 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,595 - distributed.worker - INFO -          dashboard at:         10.67.22.235:46293
2025-01-29 20:43:47,595 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,595 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-01-29 20:43:47,595 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,595 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:43:47,596 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,595 - distributed.worker - INFO -               Threads:                         10
2025-01-29 20:43:47,596 - di

2025-01-29 20:43:47,694 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,688 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-01-29 20:43:47,694 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,688 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-hl_qbrb9
2025-01-29 20:43:47,694 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,688 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:43:47,697 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,699 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.180:45629
2025-01-29 20:43:47,698 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,699 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.180:45629
2025-01-29 20:43:47,698 - distributed.deploy.ssh - INFO - 2025-01-29 20:43:47,699 - distributed.worker - INFO -          dashboard at:         10.67.22.180:34157
2025-01-29 20:4

...

2025-01-29 20:55:03,395 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,390 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:55:03,398 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,390 - distributed.worker - INFO -               Threads:                         30
2025-01-29 20:55:03,398 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,390 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-01-29 20:55:03,399 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,390 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-ym7cs52z
2025-01-29 20:55:03,399 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,390 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:55:03,401 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,401 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.180:41171
2025-01-29 20:5

2025-01-29 20:55:03,551 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,549 - distributed.worker - INFO -          Listening to:    tcp://10.67.22.72:33275
2025-01-29 20:55:03,552 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,549 - distributed.worker - INFO -          dashboard at:          10.67.22.72:35581
2025-01-29 20:55:03,553 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,549 - distributed.worker - INFO - Waiting to connect to:     tcp://10.67.22.72:8787
2025-01-29 20:55:03,554 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,549 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:55:03,554 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,549 - distributed.worker - INFO -               Threads:                         30
2025-01-29 20:55:03,555 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,549 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-01-29 20:55:03,556 - di

2025-01-29 20:55:03,643 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,640 - distributed.worker - INFO -                Memory:                   7.75 GiB
2025-01-29 20:55:03,643 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,640 - distributed.worker - INFO -       Local Directory: /tmp/dask-scratch-space/worker-2i7p9cnm
2025-01-29 20:55:03,647 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,640 - distributed.worker - INFO - -------------------------------------------------
2025-01-29 20:55:03,653 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,654 - distributed.worker - INFO -       Start worker at:   tcp://10.67.22.235:38079
2025-01-29 20:55:03,653 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,654 - distributed.worker - INFO -          Listening to:   tcp://10.67.22.235:38079
2025-01-29 20:55:03,657 - distributed.deploy.ssh - INFO - 2025-01-29 20:55:03,658 - distributed.worker - INFO -          dashboard at:         10.67.22.235:43053
2025-01-29 20:5

<Client: 'tcp://10.67.22.72:8787' processes=30 threads=900, memory=232.54 GiB>


/home/parisdiaz/.local/lib/python3.10/site-packages/dask_expr/_collection.py:4190: UserWarning: 
You did not provide metadata, so Dask is running your function on a small dataset to guess output types. It is possible that Dask will guess incorrectly.
To provide an explicit output types or to silence this message, please provide the `meta=` keyword, as described in the map or apply function that you are using.
  Before: .apply(func)
  After:  .apply(func, meta=('chamber', 'float64'))

  warnings.warn(meta_warning(meta))


In [8]:
client.close()
cluster.close()